**Enlace al Notebook del día 4 (primer día con python)**

[![Open In Colab](https://colab.research.google.com/assets/colab-badge.svg)](https://colab.research.google.com/github/Digdgeo/GEE_Course_2022/blob/main/Dia4/SDM_geemap_course_day_4.ipynb)

In [3]:
#!pip install geemap

# <font color = 'red'>**GEE Lesson 10 - Reducing an Earth Engine ImageCollection**</font> 


https://tutorials.geemap.org/ImageCollection/reducing_image_collection/

**Reducing an ImageCollection**

To composite images in an `ImageCollection`, use `imageCollection.reduce()`. This will composite all the images in the collection to a single image representing, for example, the min, max, mean or standard deviation of the images. (See the Reducers section for more information about reducers). For example, to create a median value image from a collection:

In [4]:
import ee
import geemap

ee.Authenticate()
ee.Initialize()

To authorize access needed by Earth Engine, open the following URL in a web browser and follow the instructions. If the web browser does not start automatically, please manually browse the URL below.

    https://code.earthengine.google.com/client-auth?scopes=https%3A//www.googleapis.com/auth/earthengine%20https%3A//www.googleapis.com/auth/devstorage.full_control&request_id=5vTCggCfEH3EYkBG430VXjMFzqLVp-IuV0z78OkdSro&tc=MSF92U0nNt_G7GtFV_CQr6E4AyIZN1vmK9iJ9yiosts&cc=onc-96W6I6-UIqBbtpVxH51fRzmc1XdJQVIoR5p6eL0

The authorization workflow will generate a code, which you should paste in the box below.
Enter verification code: 4/1AWtgzh6GfDQ-48r6yxCnrlvAc-P8wpAk8UK65FC3-CvP4Ry6BbYJ7X_H8VQ

Successfully saved authorization token.


In [5]:
Map = geemap.Map()
Map

Map(center=[20, 0], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=HBox(children=(Togg…

## Compute a median image

In [15]:
# Load a Landsat 8 collection for a single path-row.
collection = ee.ImageCollection('LANDSAT/LC08/C01/T1_TOA') \
    .filter(ee.Filter.eq('WRS_PATH', 202)) \
    .filter(ee.Filter.eq('WRS_ROW', 34)) \
    .filterDate('2020-01-01', '2020-12-31')

# Compute a median image and display.
median = collection.median()
Map.setCenter(-6.15, 37, 12)
Map.addLayer(median, {'bands': ['B4',  'B3',  'B2'], 'max': 0.3}, 'median')

In [16]:
collection.size().getInfo()

20

In [17]:
collection.aggregate_array("system:id").getInfo()

['LANDSAT/LC08/C01/T1_TOA/LC08_202034_20200101',
 'LANDSAT/LC08/C01/T1_TOA/LC08_202034_20200117',
 'LANDSAT/LC08/C01/T1_TOA/LC08_202034_20200202',
 'LANDSAT/LC08/C01/T1_TOA/LC08_202034_20200218',
 'LANDSAT/LC08/C01/T1_TOA/LC08_202034_20200422',
 'LANDSAT/LC08/C01/T1_TOA/LC08_202034_20200508',
 'LANDSAT/LC08/C01/T1_TOA/LC08_202034_20200524',
 'LANDSAT/LC08/C01/T1_TOA/LC08_202034_20200609',
 'LANDSAT/LC08/C01/T1_TOA/LC08_202034_20200625',
 'LANDSAT/LC08/C01/T1_TOA/LC08_202034_20200711',
 'LANDSAT/LC08/C01/T1_TOA/LC08_202034_20200727',
 'LANDSAT/LC08/C01/T1_TOA/LC08_202034_20200812',
 'LANDSAT/LC08/C01/T1_TOA/LC08_202034_20200828',
 'LANDSAT/LC08/C01/T1_TOA/LC08_202034_20200913',
 'LANDSAT/LC08/C01/T1_TOA/LC08_202034_20200929',
 'LANDSAT/LC08/C01/T1_TOA/LC08_202034_20201015',
 'LANDSAT/LC08/C01/T1_TOA/LC08_202034_20201031',
 'LANDSAT/LC08/C01/T1_TOA/LC08_202034_20201116',
 'LANDSAT/LC08/C01/T1_TOA/LC08_202034_20201202',
 'LANDSAT/LC08/C01/T1_TOA/LC08_202034_20201218']

At each location in the output image, in each band, the pixel value is the median of all unmasked pixels in the input imagery (the images in the collection). In the previous example, median() is a convenience method for the following call:

In [18]:
# Reduce the collection with a median reducer.
median = collection.reduce(ee.Reducer.median())

# Display the median image.
Map.addLayer(median,
             {'bands': ['B4_median',  'B3_median',  'B2_median'], 'max': 0.3},
             'also median')
Map

Map(bottom=408437.0, center=[37, -6.15], controls=(WidgetControl(options=['position', 'transparent_bg'], widge…

## Create an image composite

In [19]:
peninsula = ee.FeatureCollection('projects/ee-digdgeografo/assets/peninsula_iberica')
#Map.addLayer(peninsula)

In [26]:
collection = ee.ImageCollection('LANDSAT/LC08/C01/T1_TOA') \
    .filterBounds(peninsula) \
    .filterDate('2020-01-01', '2021-01-01')

In [27]:
collection.size().getInfo()

938

In [22]:
spain = peninsula.filter(ee.Filter.eq("ADM0_A3", "ESP"))
portugal = peninsula.filter(ee.Filter.eq("ADM0_A3", "PRT"))
#Map.addLayer(portugal, {}, "Portugal")

In [23]:
image = collection.median().clip(spain)
Map.addLayer(image, {'bands': ['B4',  'B3',  'B2'], 'max': 0.3}, 'Landsat 2020')

#<font color = 'red'>**GEE Lesson 11 - Using the map function with Earth Engine Image Collection**</font>

https://tutorials.geemap.org/ImageCollection/mapping_over_image_collection/

In [28]:
Map = geemap.Map()

In [29]:
def minus1000(num):
    result = ee.Number(num).subtract(1000)
    return result

In [30]:
result = minus1000(2000)
print(result.getInfo())

1000


## Apply the map function

In [31]:
years = ee.List.sequence(2000, 2010)
print(years.getInfo())

[2000, 2001, 2002, 2003, 2004, 2005, 2006, 2007, 2008, 2009, 2010]


In [32]:
results = years.map(minus1000)
print(results.getInfo())

[1000, 1001, 1002, 1003, 1004, 1005, 1006, 1007, 1008, 1009, 1010]


## Use anonymous/lambda function

In [33]:
years = ee.List.sequence(2000, 2010)

results = years.map(lambda x: ee.Number(x).subtract(1000))
print(results.getInfo())

[1000, 1001, 1002, 1003, 1004, 1005, 1006, 1007, 1008, 1009, 1010]


## Filter an ImageCollection

In [35]:
roi = ee.Geometry.Point(-5.92, 36.96)  

collection = ee.ImageCollection('LANDSAT/LC08/C01/T1_SR') \
    .filterBounds(roi) \
    .filterDate("2019-01-01", "2020-01-01") \
    .sort("CLOUD_COVER")

print(collection.size().getInfo())

25


In [36]:
image = collection.first()

In [37]:
image.getInfo()

{'type': 'Image',
 'bands': [{'id': 'B1',
   'data_type': {'type': 'PixelType',
    'precision': 'int',
    'min': -32768,
    'max': 32767},
   'dimensions': [7571, 7711],
   'crs': 'EPSG:32629',
   'crs_transform': [30, 0, 632985, 0, -30, 4266315]},
  {'id': 'B2',
   'data_type': {'type': 'PixelType',
    'precision': 'int',
    'min': -32768,
    'max': 32767},
   'dimensions': [7571, 7711],
   'crs': 'EPSG:32629',
   'crs_transform': [30, 0, 632985, 0, -30, 4266315]},
  {'id': 'B3',
   'data_type': {'type': 'PixelType',
    'precision': 'int',
    'min': -32768,
    'max': 32767},
   'dimensions': [7571, 7711],
   'crs': 'EPSG:32629',
   'crs_transform': [30, 0, 632985, 0, -30, 4266315]},
  {'id': 'B4',
   'data_type': {'type': 'PixelType',
    'precision': 'int',
    'min': -32768,
    'max': 32767},
   'dimensions': [7571, 7711],
   'crs': 'EPSG:32629',
   'crs_transform': [30, 0, 632985, 0, -30, 4266315]},
  {'id': 'B5',
   'data_type': {'type': 'PixelType',
    'precision': 'in

In [38]:
geemap.image_props(image).getInfo()

{'CLOUD_COVER': 0.01,
 'CLOUD_COVER_LAND': 0.01,
 'EARTH_SUN_DISTANCE': 1.01373,
 'ESPA_VERSION': '2_23_0_1b',
 'GEOMETRIC_RMSE_MODEL': 7.863,
 'GEOMETRIC_RMSE_MODEL_X': 5.493,
 'GEOMETRIC_RMSE_MODEL_Y': 5.626,
 'IMAGE_DATE': '2019-08-10',
 'IMAGE_QUALITY_OLI': 9,
 'IMAGE_QUALITY_TIRS': 9,
 'LANDSAT_ID': 'LC08_L1TP_202034_20190810_20190820_01_T1',
 'LEVEL1_PRODUCTION_DATE': 1566303725000,
 'NOMINAL_SCALE': 30,
 'PIXEL_QA_VERSION': 'generate_pixel_qa_1.6.0',
 'SATELLITE': 'LANDSAT_8',
 'SENSING_TIME': '2019-08-10T11:02:39.9555230Z',
 'SOLAR_AZIMUTH_ANGLE': 132.630096,
 'SOLAR_ZENITH_ANGLE': 29.232498,
 'SR_APP_VERSION': 'LaSRC_1.3.0',
 'WRS_PATH': 202,
 'WRS_ROW': 34,
 'system:asset_size': '630.995513 MB',
 'system:band_names': ['B1',
  'B2',
  'B3',
  'B4',
  'B5',
  'B6',
  'B7',
  'B10',
  'B11',
  'sr_aerosol',
  'pixel_qa',
  'radsat_qa'],
 'system:id': 'LANDSAT/LC08/C01/T1_SR/LC08_202034_20190810',
 'system:index': 'LC08_202034_20190810',
 'system:time_end': '2019-08-10 11:02:39',

In [39]:
collection.aggregate_array("CLOUD_COVER").getInfo()

[0.01,
 0.01,
 0.03,
 0.05,
 0.37,
 0.83,
 1.06,
 1.11,
 1.33,
 2.29,
 2.39,
 2.47,
 2.68,
 4.25,
 4.62,
 7.06,
 7.74,
 19.76,
 29.08,
 29.3,
 36.03,
 48.63,
 58.58,
 66.22,
 98.19]

In [40]:
#Map = geemap.Map()
vis_params = {
    'bands': ['B5', 'B4', 'B3'],
    'min': 0, 
    'max': 3000,
    'gamma': 1.0
}

Map.addLayer(image, vis_params, "First image")
Map.centerObject(image)
Map

Map(center=[20, 0], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=HBox(children=(Togg…

## Select the best image each year

In [41]:
roi = ee.Geometry.Point(-5.99, 36.96)

def best_image(year):
    start_date = ee.Date.fromYMD(year, 1, 1)
    end_date = start_date.advance(1, 'year')
    
    image = ee.ImageCollection('LANDSAT/LC08/C01/T1_SR') \
        .filterBounds(roi) \
        .filterDate(start_date, end_date) \
        .sort("CLOUD_COVER") \
        .first()
    
    return image

In [42]:
start_year = 2013
end_year = 2020
years = ee.List.sequence(start_year, end_year)
year_list = years.getInfo()
print(year_list)

[2013, 2014, 2015, 2016, 2017, 2018, 2019, 2020]


In [43]:
images = years.map(best_image)

In [44]:
count = images.size().getInfo()
print(count)

8


In [45]:
ee.ImageCollection(images).aggregate_array("CLOUD_COVER").getInfo()

[0, 0, 0.01, 0, 0, 0, 0.01, 0.09]

In [55]:
ee.ImageCollection(images).aggregate_array("system:id").getInfo()

['LANDSAT/LC08/C01/T1_SR/LC08_202034_20130724',
 'LANDSAT/LC08/C01/T1_SR/LC08_202034_20140812',
 'LANDSAT/LC08/C01/T1_SR/LC08_202034_20150730',
 'LANDSAT/LC08/C01/T1_SR/LC08_202034_20160801',
 'LANDSAT/LC08/C01/T1_SR/LC08_202034_20170804',
 'LANDSAT/LC08/C01/T1_SR/LC08_202034_20180924',
 'LANDSAT/LC08/C01/T1_SR/LC08_202034_20190810',
 'LANDSAT/LC08/C01/T1_SR/LC08_202034_20201031']

In [52]:
for index in range(0, count):
    image = ee.Image(images.get(index))
    layer_name = "Image " + str(year_list[index])
    print(layer_name)
    Map.addLayer(image, vis_params, layer_name, False)

Image 2013
Image 2014
Image 2015
Image 2016
Image 2017
Image 2018
Image 2019
Image 2020


In [51]:
Map = geemap.Map(height=1200)
Map

Map(center=[20, 0], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=HBox(children=(Togg…

## Set image properties

In [56]:
collection = ee.ImageCollection(images)

In [57]:
collection.aggregate_array("system:time_start").getInfo()

[1374663871570,
 1407841356543,
 1438254130360,
 1470049354510,
 1501844552565,
 1537786934040,
 1565434959955,
 1604142172552]

In [58]:
collection = collection.map(lambda img: img.set({"DATE": ee.Date(img.get("system:time_start")).format("YYYY-MM-dd")}))

In [59]:
collection.aggregate_array("DATE").getInfo()

['2013-07-24',
 '2014-08-12',
 '2015-07-30',
 '2016-08-01',
 '2017-08-04',
 '2018-09-24',
 '2019-08-10',
 '2020-10-31']

# <font color = 'red'>**GEE Lesson 12. Creating time-series cloud-free image composite**</font>

https://tutorials.geemap.org/ImageCollection/cloud_free_composite/

In [60]:
Map = geemap.Map(height=1000)
Map

Map(center=[20, 0], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=HBox(children=(Togg…

In [61]:
years = ee.List.sequence(2013, 2020)
years.getInfo()

[2013, 2014, 2015, 2016, 2017, 2018, 2019, 2020]

In [64]:
def yearly_image(year):
    
    start_date = ee.Date.fromYMD(year, 1, 1) 
    end_date = start_date.advance(1, "year")
    
    collection = ee.ImageCollection('LANDSAT/LC08/C01/T1') \
        .filterDate(start_date, end_date) \
        .filterBounds(portugal) 
    
    image =  ee.Algorithms.Landsat.simpleComposite(collection).clipToCollection(portugal)

    return image

In [65]:
images = years.map(yearly_image)

In [66]:
vis_params = {
    'bands': ['B6', 'B5', 'B2'],
    'min': 0, 
    'max': 150,
    'gamma': 1.0
}

for index in range(0, 8):
    image = ee.Image(images.get(index))
    layer_name = "Image " + str(index + 2013)
    Map.addLayer(image, vis_params, layer_name)

# <font color='red'>**GEE Lesson 13 - Visualizing Earth Engine time-series images**</font>


https://tutorials.geemap.org/ImageCollection/visualizing_time_series/

## Visualizing weather data

In [69]:
Map = geemap.Map()

collection = ee.ImageCollection('NOAA/GFS0P25') \
  .filterDate('2021-07-22', '2021-07-23') \
  .limit(24) \
  .select('temperature_2m_above_ground')

vis_params = {
  'min': -40.0,
  'max': 35.0,
  'palette': ['blue', 'purple', 'cyan', 'green', 'yellow', 'red']
}

first_image = collection.first()

Map.addLayer(first_image, vis_params, "First image")
Map.setCenter(-0.3490, 25.7900, 2)
Map

Map(center=[25.79, -0.349], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=HBox(childr…

In [72]:
image = collection.toBands()
Map.addLayer(image, {}, "Time series", False)

In [73]:
labels = [str(n).zfill(2) + ":00" for n in range(0, 24)]
labels

['00:00',
 '01:00',
 '02:00',
 '03:00',
 '04:00',
 '05:00',
 '06:00',
 '07:00',
 '08:00',
 '09:00',
 '10:00',
 '11:00',
 '12:00',
 '13:00',
 '14:00',
 '15:00',
 '16:00',
 '17:00',
 '18:00',
 '19:00',
 '20:00',
 '21:00',
 '22:00',
 '23:00']

In [74]:
Map.add_time_slider(collection, vis_params, labels=labels, time_interval=1)
Map

Map(bottom=1626.0, center=[53.43214904472838, 253.75328516083079], controls=(WidgetControl(options=['position'…

## Visualizing vegetation data

In [85]:
Map = geemap.Map()

collection = ee.ImageCollection('MODIS/MCD43A4_006_NDVI') \
                  .filter(ee.Filter.date('2018-04-01', '2018-06-30')) \
                  .select("NDVI")\

vis_params = {
  'min': 0.0,
  'max': 1.0,
  'palette': [
    'FFFFFF', 'CE7E45', 'DF923D', 'F1B555', 'FCD163', '99B718', '74A901',
    '66A000', '529400', '3E8601', '207401', '056201', '004C00', '023B01',
    '012E01', '011D01', '011301'
  ],
}

first_image = collection.first()

Map.addLayer(first_image, vis_params, "First image")
Map.setCenter(-7.03125, 31.0529339857, 2)
Map

Map(center=[31.0529339857, -7.03125], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=H…

Element.toDictionary: Parameter 'element' is required.
Element.toDictionary: Parameter 'element' is required.


In [86]:
image = collection.toBands()
Map.addLayer(image, {}, "Time series", False)

In [88]:
labels = collection.aggregate_array("system:index").getInfo()
Map.add_time_slider(collection, vis_params, labels=labels, time_interval=1)

## Visualizing Landsat imagery

In [89]:
Map = geemap.Map()

bands = ['B1', 'B2', 'B3', 'B4', 'B5', 'B7']
image = ee.Image('LE7_TOA_5YEAR/1999_2003').select(bands)
vis_params = {'min': 20, 'max': 200, 'gamma': 2.0}

Map.add_time_slider(image, vis_params, labels=bands, time_interval=1)

Map

Map(center=[20, 0], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=HBox(children=(Togg…

#<font color = 'red'>**GEE Lesson 14 - Exporting Earth Engine data**</font>


https://tutorials.geemap.org/AssetManagement/export_data/

In [90]:
import os
from geemap.datasets import DATA

In [91]:
Map = geemap.Map()

## Set an output directory

In [92]:
out_dir = os.path.expanduser("~/Downloads")

if not os.path.exists(out_dir):
    os.makedirs(out_dir)

In [93]:
out_dir = os.path.expanduser("~/Downloads")
filename = os.path.join(out_dir, 'landsat.tif')
print(filename)

/root/Downloads/landsat.tif


## Export an ee.FeatureCollection

In [95]:
fc = ee.FeatureCollection('users/giswqs/public/countries')

In [96]:
Map.addLayer(fc, {}, "Countries")
Map.centerObject(fc)
Map

Map(center=[20, 0], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=HBox(children=(Togg…

Export data to a local computer

In [97]:
out_shp = os.path.join(out_dir, "countries.shp")
geemap.ee_export_vector(fc, out_shp, verbose=True)

Generating URL ...
Please wait ...
An error occurred while downloading. 
 Retrying ...
Generating URL ...
Please wait ...
Data downloaded to /root/Downloads/countries.shp


Export data to Google Drive

In [ ]:
geemap.ee_export_vector_to_drive(fc, description="countries", folder="export")

Exporting countries...


## Export an ee.Image

In [98]:
image = ee.Image('LE7_TOA_5YEAR/1999_2003')

landsat_vis = {
    'bands': ['B4', 'B3', 'B2'], 
    'gamma': 1.7
}
Map.addLayer(image, landsat_vis, "LE7_TOA_5YEAR/1999_2003", True, 1)
Map

Map(bottom=536.0, center=[14.016649062891737, 0.0], controls=(WidgetControl(options=['position', 'transparent_…

In [99]:
out_dir = os.path.expanduser("~/Downloads")
filename = os.path.join(out_dir, 'landsat.tif')
#print(filename)

### Exporting all bands as one single image

In [100]:
# Draw any shapes on the map using the Drawing tools before executing this code block
roi = Map.user_roi

In [101]:
roi.getInfo()

{'type': 'Polygon',
 'coordinates': [[[-366.816148, 36.752289],
   [-365.887284, 36.752289],
   [-365.887284, 37.572091],
   [-366.816148, 37.572091],
   [-366.816148, 36.752289]]]}

In [102]:
image_clip = image.clip(roi)

In [103]:
Map.addLayer(image_clip, landsat_vis, "image")

In [104]:
geemap.ee_export_image(image_clip, filename=filename, scale=90, region=roi, file_per_band=False)

Generating URL ...
Please wait ...
Data downloaded to /root/Downloads/landsat.tif


### Exporting each band as one image

In [ ]:
geemap.ee_export_image(image, filename=filename, scale=90, region=roi, file_per_band=True)

Generating URL ...
Please wait ...
Data downloaded to /root/Downloads


### Export an image to Google Drive

In [ ]:
geemap.ee_export_image_to_drive(image_clip, description='landsat', folder='export', region=roi, scale=30)

Exporting landsat ...


## Download an ee.ImageCollection

In [105]:
loc = ee.Geometry.Point(-99.2222, 46.7816)
collection = ee.ImageCollection('USDA/NAIP/DOQQ') \
    .filterBounds(loc) \
    .filterDate('2008-01-01', '2020-01-01') \
    .filter(ee.Filter.listContains("system:band_names", "N"))

In [ ]:
out_dir = os.path.expanduser('~/Downloads')

In [106]:
collection.aggregate_array('system:index').getInfo()

['m_4609915_sw_14_060_20180902_20181213',
 'm_4609915_sw_14_060_20190626',
 'm_4609915_sw_14_1_20090818',
 'm_4609915_sw_14_1_20100629',
 'm_4609915_sw_14_1_20120714',
 'm_4609915_sw_14_1_20140901',
 'm_4609915_sw_14_1_20150926',
 'm_4609915_sw_14_h_20160704',
 'm_4609915_sw_14_h_20170703']

In [109]:
geemap.ee_export_image_collection(collection, scale=5, out_dir=out_dir)

Total number of images: 9

Exporting 1/9: m_4609915_sw_14_060_20180902_20181213.tif
Generating URL ...
Please wait ...
Data downloaded to /root/Downloads/m_4609915_sw_14_060_20180902_20181213.tif


Exporting 2/9: m_4609915_sw_14_060_20190626.tif
Generating URL ...
Please wait ...
Data downloaded to /root/Downloads/m_4609915_sw_14_060_20190626.tif


Exporting 3/9: m_4609915_sw_14_1_20090818.tif
Generating URL ...
Please wait ...
Data downloaded to /root/Downloads/m_4609915_sw_14_1_20090818.tif


Exporting 4/9: m_4609915_sw_14_1_20100629.tif
Generating URL ...
Please wait ...
Data downloaded to /root/Downloads/m_4609915_sw_14_1_20100629.tif


Exporting 5/9: m_4609915_sw_14_1_20120714.tif
Generating URL ...
Please wait ...
Data downloaded to /root/Downloads/m_4609915_sw_14_1_20120714.tif


Exporting 6/9: m_4609915_sw_14_1_20140901.tif
Generating URL ...
Please wait ...
Data downloaded to /root/Downloads/m_4609915_sw_14_1_20140901.tif


Exporting 7/9: m_4609915_sw_14_1_20150926.tif
Generat

In [ ]:
geemap.ee_export_image_collection_to_drive(collection, folder='export', scale=10)

Total number of images: 9

Exporting m_4609915_sw_14_060_20180902_20181213 ...
Exporting m_4609915_sw_14_060_20190626 ...
Exporting m_4609915_sw_14_1_20090818 ...
Exporting m_4609915_sw_14_1_20100629 ...
Exporting m_4609915_sw_14_1_20120714 ...
Exporting m_4609915_sw_14_1_20140901 ...
Exporting m_4609915_sw_14_1_20150926 ...
Exporting m_4609915_sw_14_h_20160704 ...
Exporting m_4609915_sw_14_h_20170703 ...


## Extract pixels as a Numpy array

In [110]:
import numpy as np
import matplotlib.pyplot as plt

img = ee.Image('LANDSAT/LC08/C01/T1_SR/LC08_038029_20180810') \
  .select(['B4', 'B5', 'B6'])

aoi = ee.Geometry.Polygon(
  [[[-110.8, 44.7],
    [-110.8, 44.6],
    [-110.6, 44.6],
    [-110.6, 44.7]]], None, False)

rgb_img = geemap.ee_to_numpy(img, region=aoi)
print(rgb_img.shape)

(373, 531, 3)


# <font color = 'red'>**GEE Lesson 15 - Styling Earth Engine vector data**</font>

https://tutorials.geemap.org/FeatureCollection/vector_styling/

In [112]:
Map = geemap.Map()

Map.addLayer(fc, {}, "Countries")
Map

Map(center=[20, 0], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=HBox(children=(Togg…

## Use Image.paint()

In [113]:
Map = geemap.Map()

image = ee.Image().paint(fc, 0, 1)

Map.addLayer(image, {'palette': 'red'}, "Countries")
Map

Map(center=[20, 0], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=HBox(children=(Togg…

## Use FeatureCollection.style()

In [114]:
Map = geemap.Map()

style = {'color': '0000ffff', 'width': 4, 'lineType': 'solid', 'fillColor': '00000080'}

Map.addLayer(fc.style(**style), {}, "US States")
Map

Map(center=[20, 0], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=HBox(children=(Togg…

## Use add_styled_vector()

In [116]:
Map = geemap.Map()

vis_params = {
    'color': '000000', 
    'colorOpacity': 1,
    'pointSize': 3,
    'pointShape': 'circle',
    'width': 2,
    'lineType': 'solid', 
    'fillColorOpacity': 0.75    
}

palette = ['006633', 'E5FFCC', '662A00', 'D8D8D8', 'F5F5F5']

Map.add_styled_vector(fc, column="SUBREGION", palette=palette, layer_name="Styled vector", **vis_params)
Map

Map(center=[20, 0], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=HBox(children=(Togg…

In [117]:
import geemap.colormaps as cm

In [119]:
Map = geemap.Map()


vis_params = {
    'color': '000000', 
    'colorOpacity': 1,
    'pointSize': 3,
    'pointShape': 'circle',
    'width': 2,
    'lineType': 'dotted', 
    'fillColorOpacity': 0.66    
}

palette = list(cm.palettes.gist_earth.n12)

Map.add_styled_vector(fc, column="CONTINENT", palette=palette, layer_name="Styled vector", **vis_params)
Map

Map(center=[20, 0], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=HBox(children=(Togg…

## Use interactive GUI

In [121]:
Map = geemap.Map()

Map.addLayer(fc, {}, "Countries")
Map

Map(center=[20, 0], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=HBox(children=(Togg…

# <font color = 'red'>**GEE Lesson 16 - Extracting time-series pixel values from Earth Engine Image**</font>


https://tutorials.geemap.org/AssetManagement/extract_values/

In [129]:
Map = geemap.Map()
Map

Map(center=[20, 0], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=HBox(children=(Togg…

In [130]:
landsat7 = ee.Image('LE7_TOA_5YEAR/1999_2003') \
    .select([0, 1, 2, 3, 4, 6])
landsat_vis = {
    'bands': ['B4', 'B3', 'B2'], 
    'gamma': 1.7
}
Map.addLayer(landsat7, landsat_vis, "LE7_TOA_5YEAR/1999_2003")

Map.set_plot_options(add_marker_cluster=True)

### Export pixel values to shapefile/csv

In [131]:
out_dir = os.path.expanduser('~/Downloads')
# out_csv = os.path.join(out_dir, 'points.csv')
out_shp = os.path.join(out_dir, 'points.shp')
print(out_shp)

/root/Downloads/points.shp


In [132]:
Map.extract_values_to_points(out_shp)

In [127]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


## Interactive Region Reduction

In [133]:
import geemap.colormaps as cm

In [134]:
m = geemap.Map()

In [135]:
collection = ee.ImageCollection('MODIS/006/MOD13A2') \
    .filterDate('2015-01-01', '2019-12-31') \
    .select('NDVI')

# Convert the image collection to an image.
image = collection.toBands()

palette = cm.palettes.ndvi

ndvi_vis = {
  'min': 0.0,
  'max': 9000.0,
  'palette': palette
}

m.addLayer(image, {}, 'MODIS NDVI Time-series')
m.addLayer(image.select(0), ndvi_vis, 'MODIS NDVI VIS')

m

Map(center=[20, 0], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=HBox(children=(Togg…

In [136]:
m.set_plot_options(add_marker_cluster=True, marker=None)
m.roi_reducer = ee.Reducer.mean()

### Export data

In [137]:
out_dir = os.path.expanduser('~/Downloads')
# out_csv = os.path.join(out_dir, 'points.csv')
out_shp = os.path.join(out_dir, 'ndvi.shp')
m.extract_values_to_points(out_shp)

## Creating training samples

In [ ]:
geemap.show_youtube("https://youtu.be/VWh5PxXPZw0")

Output(layout=Layout(width='815px'))

In [ ]:
Map = geemap.Map()
Map

Map(center=[20, 0], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=HBox(children=(Togg…

In [ ]:
Map.user_rois.getInfo()

In [138]:
out_dir = os.path.expanduser('~/Downloads')
out_shp = os.path.join(out_dir, 'collections_sample.shp')

In [139]:
geemap.ee_to_shp(Map.user_rois, out_shp)

Generating URL ...
Please wait ...
Data downloaded to /root/Downloads/collections_sample.shp


## <font color = 'red'>**GEE Lesson 18. Computing zonal statistics with Google Earth Engine**</font>

https://tutorials.geemap.org/Analysis/zonal_statistics/

In [140]:
Map = geemap.Map()
Map

Map(center=[20, 0], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=HBox(children=(Togg…

In [141]:
# Add Earth Engine dataset
dem = ee.Image('USGS/SRTMGL1_003')

# Set visualization parameters.
dem_vis = {
  'min': 0,
  'max': 4000,
  'palette': ['006633', 'E5FFCC', '662A00', 'D8D8D8', 'F5F5F5']}

# Add Earth Engine DEM to map
Map.addLayer(dem, dem_vis, 'SRTM DEM')

# Add Landsat data to map
landsat = ee.Image('LE7_TOA_5YEAR/1999_2003')

landsat_vis = {
    'bands': ['B4', 'B3', 'B2'], 
    'gamma': 1.4
}
Map.addLayer(landsat, landsat_vis, "Landsat", False)

Map.addLayer(fc, {}, 'countries')

## Compute zonal statistics for one image

In [ ]:
out_dir = os.path.expanduser('~/Downloads')
if not os.path.exists(out_dir):
    os.makedirs(out_dir)

In [142]:
out_dem_stats = os.path.join(out_dir, 'dem_stats.csv')  

# Allowed output formats: csv, shp, json, kml, kmz
# Allowed statistics type: MEAN, MAXIMUM, MINIMUM, MEDIAN, STD, MIN_MAX, VARIANCE, SUM
geemap.zonal_statistics(dem, fc, out_dem_stats, statistics_type='MEAN', scale=1000)

Computing statistics ...
Generating URL ...
Please wait ...
Data downloaded to /root/Downloads/dem_stats.csv


In [ ]:
out_landsat_stats = os.path.join(out_dir, 'landsat_stats.csv')  
geemap.zonal_statistics(landsat, states, out_landsat_stats, statistics_type='SUM', scale=1000)

## Compute zonal statistics for time-series images

In [143]:
Map = geemap.Map()

collection = ee.ImageCollection('MODIS/MCD43A4_006_NDVI') \
                  .filter(ee.Filter.date('2018-04-01', '2018-05-01')) \
                  .select("NDVI")\

vis_params = {
  'min': 0.0,
  'max': 1.0,
  'palette': [
    'FFFFFF', 'CE7E45', 'DF923D', 'F1B555', 'FCD163', '99B718', '74A901',
    '66A000', '529400', '3E8601', '207401', '056201', '004C00', '023B01',
    '012E01', '011D01', '011301'
  ],
}

first_image = collection.first()

Map.addLayer(first_image, vis_params, "First image")
Map.setCenter(-7.03125, 31.0529339857, 2)
Map

Map(center=[31.0529339857, -7.03125], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=H…

In [144]:
modis = collection.toBands()
Map.addLayer(modis, {}, "MODIS Time series", False)

In [145]:
out_landsat_stats = os.path.join(out_dir, 'ndvi.csv')  
geemap.zonal_statistics(modis, fc, out_landsat_stats, statistics_type='MEAN', scale=1000)

Computing statistics ...
Generating URL ...


Please wait ...
Data downloaded to /root/Downloads/ndvi.csv


In [ ]:
out_landsat_stats = os.path.join(out_dir, 'ndvi.csv')  
geemap.zonal_statistics(modis, fc, out_landsat_stats, statistics_type='MEAN', scale=1000)

Computing statistics ...
Generating URL ...
Please wait ...
Data downloaded to /root/Downloads/ndvi.csv


# <font color = 'red'>**GEE Lesson 19 - Computing zonal statistics by group with Google Earth Engine**</font>

https://tutorials.geemap.org/Analysis/zonal_stats_by_group/

In [147]:
Map = geemap.Map()
Map

Map(center=[20, 0], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=HBox(children=(Togg…

### Add NLCD data

NLCD: USGS National Land Cover Database

https://developers.google.com/earth-engine/datasets/catalog/USGS_NLCD_RELEASES_2016_REL

In [148]:
dataset = ee.Image('USGS/NLCD/NLCD2016')
landcover = ee.Image(dataset.select('landcover'))
Map.addLayer(landcover, {}, 'NLCD 2016')

states = ee.FeatureCollection("TIGER/2018/States")
Map.addLayer(states, {}, 'US States')

In [149]:
Map.add_legend(builtin_legend='NLCD')

### Calculate land cover compostion of each US state

In [ ]:
out_dir = os.path.expanduser('~/Downloads')
if not os.path.exists(out_dir):
    os.makedirs(out_dir)

In [ ]:
nlcd_stats = os.path.join(out_dir, 'nlcd_stats_sum.csv')  
    
# statistics_type can be either 'SUM' or 'PERCENTAGE'
# denominator can be used to convert square meters to other areal units, such as square kilimeters
geemap.zonal_statistics_by_group(landcover, states, nlcd_stats, statistics_type='SUM', denominator=1000000, decimal_places=2)

Computing ... 
Generating URL ...
Please wait ...
Data downloaded to /root/Downloads/nlcd_stats_sum.csv


In [ ]:
nlcd_stats = os.path.join(out_dir, 'nlcd_stats_pct.csv')  
geemap.zonal_statistics_by_group(landcover, states, nlcd_stats, statistics_type='PERCENTAGE')

## Analyzing Global Land Cover

### Add MODIS global land cover data

MCD12Q1.006 MODIS Land Cover Type Yearly Global 500m

https://developers.google.com/earth-engine/datasets/catalog/MODIS_006_MCD12Q1

In [ ]:
Map = geemap.Map()

landcover = ee.Image('MODIS/006/MCD12Q1/2019_01_01') \
    .select('LC_Type1')

igbpLandCoverVis = {
  'min': 1.0,
  'max': 17.0,
  'palette': [
    '05450a', '086a10', '54a708', '78d203', '009900', 'c6b044', 'dcd159',
    'dade48', 'fbff13', 'b6ff05', '27ff87', 'c24f44', 'a5a5a5', 'ff6d4c',
    '69fff8', 'f9ffa4', '1c0dff'
  ],
}

Map.setCenter(6.746, 46.529, 2)
Map.addLayer(landcover, igbpLandCoverVis, 'MODIS Land Cover')

countries = ee.FeatureCollection('users/giswqs/public/countries')
Map.addLayer(countries, {}, "Countries")

Map

Map(center=[46.529, 6.746], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=HBox(childr…

In [ ]:
Map.add_legend(builtin_legend='MODIS/051/MCD12Q1')

In [ ]:
out_dir = os.path.join(os.path.expanduser('~'), 'Downloads')
global_stats = os.path.join(out_dir, 'global_stats_sum.csv')  

# statistics_type can be either 'SUM' or 'PERCENTAGE'
# denominator can be used to convert square meters to other areal units, such as square kilimeters
geemap.zonal_statistics_by_group(landcover, countries, global_stats, statistics_type='SUM', denominator=1000000, decimal_places=2)

Computing ... 
Generating URL ...
Please wait ...
Data downloaded to /root/Downloads/global_stats_sum.csv
